In [1]:
!pip install openpyxl==3.0.9 scikit-learn==0.24.2 pandas==1.1.5 lightgbm==3.2.1

Для работы ноутбука необходимо:
* Положить исходные даныне в папку ../data/*
* Положить даные по зарплатам в регионах в папку ../data/enrichment/* (скачать из https://rosstat.gov.ru/labor_market_employment_salaries - "Среднемесячная номинальная начисленная заработная плата работников по полному кругу организаций.."). Дополнительно: удалил первые пару строк из таблицы "с 2019", проставил даты вместо названия месяца (первый день месяца, например 01.01.2019).

In [2]:
# нужные библиотеки
import numpy as np
import pandas as pd
import gc
import random
import re
import typing
import numpy as np

from sklearn.model_selection import KFold
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import PolynomialFeatures
from sklearn.metrics import mean_absolute_percentage_error, r2_score, mean_squared_error

import lightgbm as lgbm

pd.set_option("display.max_rows", 100)
pd.set_option("display.max_columns", 100)

In [3]:
# реализация метрики от организаторов
THRESHOLD = 0.15
NEGATIVE_WEIGHT = 1.1

def deviation_metric_one_sample(y_true: typing.Union[float, int], y_pred: typing.Union[float, int]) -> float:
    """
    Реализация кастомной метрики для хакатона.

    :param y_true: float, реальная цена
    :param y_pred: float, предсказанная цена
    :return: float, значение метрики
    """
    deviation = (y_pred - y_true) / np.maximum(1e-8, y_true)
    if np.abs(deviation) <= THRESHOLD:
        return 0
    elif deviation <= - 4 * THRESHOLD:
        return 9 * NEGATIVE_WEIGHT
    elif deviation < -THRESHOLD:
        return NEGATIVE_WEIGHT * ((deviation / THRESHOLD) + 1) ** 2
    elif deviation < 4 * THRESHOLD:
        return ((deviation / THRESHOLD) - 1) ** 2
    else:
        return 9


def deviation_metric(y_true: np.array, y_pred: np.array) -> float:
    return np.array([deviation_metric_one_sample(y_true[n], y_pred[n]) for n in range(len(y_true))]).mean()


def median_absolute_percentage_error(y_true: np.array, y_pred: np.array) -> float:
    return np.median(np.abs(y_pred-y_true)/y_true)


def metrics_stat(y_true: np.array, y_pred: np.array) -> typing.Dict[str,float]:
    mape = mean_absolute_percentage_error(y_true, y_pred)
    mdape = median_absolute_percentage_error(y_true, y_pred)
    rmse = mean_squared_error(y_true, y_pred, squared=False)
    r2 = r2_score(y_true, y_pred)
    raif_metric = deviation_metric(y_true, y_pred)
    return {'mape':mape, 'mdape':mdape, 'rmse': rmse, 'r2': r2, 'raif_metric':raif_metric}

In [4]:
TARGET = 'per_square_meter_price'

In [5]:
train = pd.read_csv('../data/train.csv', parse_dates=['date'])
test = pd.read_csv('../data/test.csv', parse_dates=['date'])
test_submission = pd.read_csv('../data/test_submission.csv')
full_train = train.copy()

E:\pet-project\raifhack\.venv\lib\site-packages\IPython\core\interactiveshell.py:3169: DtypeWarning: Columns (1) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


# Обработка данных

In [6]:
# преобразование даты к первому числу месяца
train['date_start_month'] = train['date'].dt.date.apply(lambda x: x.replace(day=1).strftime('%Y-%m-%d'))
test['date_start_month'] = test['date'].dt.date.apply(lambda x: x.replace(day=1).strftime('%Y-%m-%d'))

In [7]:
# заменим иероглифы, чтобы lgbm в будущем не ругался
train.loc[train['osm_city_nearest_name'] == '饶河县', 'osm_city_nearest_name'] = 'неизвестно'
# приведем города к нижнему регистру
train['city'] = train['city'].str.lower()
test['city'] = test['city'].str.lower()
# оставим только те города, что есть в тесте
train = train[train['city'].isin(test['city'])]
# оставим только цены по типу 1
train = train[train['price_type'] == 1].reset_index(drop=True)

## Парсинг этажей

In [8]:
# почистим признак floor
def parsing_floor(values):
    return values.mask(values == '-1.0', -1) \
          .mask(values == '-2.0', -2) \
          .mask(values == '-3.0', -3) \
          .mask(values == 'подвал, 1', 1) \
          .mask(values == 'подвал', -1) \
          .mask(values == 'цоколь, 1', 1) \
          .mask(values == '1,2,антресоль', 1) \
          .mask(values == 'цоколь', 0) \
          .mask(values == 'тех.этаж (6)', 6) \
          .mask(values == 'Подвал', -1) \
          .mask(values == 'Цоколь', 0) \
          .mask(values == 'фактически на уровне 1 этажа', 1) \
          .mask(values == '1,2,3', 1) \
          .mask(values == '1, подвал', 1) \
          .mask(values == '1,2,3,4', 1) \
          .mask(values == '1,2', 1) \
          .mask(values == '1,2,3,4,5', 1) \
          .mask(values == '5, мансарда', 5) \
          .mask(values == '1-й, подвал', 1) \
          .mask(values == '1, подвал, антресоль', 1) \
          .mask(values == 'мезонин', 2) \
          .mask(values == 'подвал, 1-3', 1) \
          .mask(values == '1 (Цокольный этаж)', 0) \
          .mask(values == '3, Мансарда (4 эт)', 3) \
          .mask(values == 'подвал,1', 1) \
          .mask(values == '1, антресоль', 1) \
          .mask(values == '1-3', 1) \
          .mask(values == 'мансарда (4эт)', 4) \
          .mask(values == '1, 2.', 1) \
          .mask(values == 'подвал , 1 ', 1) \
          .mask(values == '1, 2', 1) \
          .mask(values == 'подвал, 1,2,3', 1) \
          .mask(values == '1 + подвал (без отделки)', 1) \
          .mask(values == 'мансарда', 3) \
          .mask(values == '2,3', 2) \
          .mask(values == '4, 5', 4) \
          .mask(values == '1-й, 2-й', 1) \
          .mask(values == '1 этаж, подвал', 1) \
          .mask(values == '1, цоколь', 1) \
          .mask(values == 'подвал, 1-7, техэтаж', 1) \
          .mask(values == '3 (антресоль)', 3) \
          .mask(values == '1, 2, 3', 1) \
          .mask(values == 'Цоколь, 1,2(мансарда)', 1) \
          .mask(values == 'подвал, 3. 4 этаж', 3) \
          .mask(values == 'подвал, 1-4 этаж', 1) \
          .mask(values == 'подва, 1.2 этаж', 1) \
          .mask(values == '2, 3', 2) \
          .mask(values == '7,8', 7) \
          .mask(values == '1 этаж', 1) \
          .mask(values == '1-й', 1) \
          .mask(values == '3 этаж', 3) \
          .mask(values == '4 этаж', 4) \
          .mask(values == '5 этаж', 5) \
          .mask(values == 'подвал,1,2,3,4,5', 1) \
          .mask(values == 'подвал, цоколь, 1 этаж', 1) \
          .mask(values == '3, мансарда', 3) \
          .mask(values == 'цоколь, 1, 2,3,4,5,6', 1) \
          .mask(values == ' 1, 2, Антресоль', 1) \
          .mask(values == '3 этаж, мансарда (4 этаж)', 3) \
          .mask(values == 'цокольный', 0) \
          .mask(values == '1,2 ', 1) \
          .mask(values == '3,4', 3) \
          .mask(values == 'подвал, 1 и 4 этаж', 1) \
          .mask(values == '5(мансарда)', 5) \
          .mask(values == 'технический этаж,5,6', 5) \
          .mask(values == ' 1-2, подвальный', 1) \
          .mask(values == '1, 2, 3, мансардный', 1) \
          .mask(values == 'подвал, 1, 2, 3', 1) \
          .mask(values == '1,2,3, антресоль, технический этаж', 1) \
          .mask(values == '3, 4', 3) \
          .mask(values == '1-3 этажи, цоколь (188,4 кв.м), подвал (104 кв.м)', 1) \
          .mask(values == '1,2,3,4, подвал', 1) \
          .mask(values == '2-й', 2) \
          .mask(values == '1, 2 этаж', 1) \
          .mask(values == 'подвал, 1, 2', 1) \
          .mask(values == '1-7', 1) \
          .mask(values == '1 (по док-м цоколь)', 1) \
          .mask(values == '1,2,подвал ', 1) \
          .mask(values == 'подвал, 2', 2) \
          .mask(values == 'подвал,1,2,3', 1) \
          .mask(values == '1,2,3 этаж, подвал ', 1) \
          .mask(values == '1,2,3 этаж, подвал', 1) \
          .mask(values == '2, 3, 4, тех.этаж', 2) \
          .mask(values == 'цокольный, 1,2', 1) \
          .mask(values == 'Техническое подполье', -1) \
          .mask(values == '1.2', 1) \
          .astype(float)
    
train['floor'] = parsing_floor(train['floor'])
test['floor'] = parsing_floor(test['floor'])

## Добавляем данные по зарплатам со двигов в 3-4 месяца

In [9]:
region_map_dict = {
    'г.Москва': 'Москва',
    'Краснодарский край': 'Краснодарский край',
    'г.Санкт-Петербург': 'Санкт-Петербург',
    'Московская область': 'Московская область',
    'Свердловская область': 'Свердловская область',
    'Челябинская область': 'Челябинская область',
    'Республика Татарстан': 'Татарстан',
    'Самарская область': 'Самарская область',
    'Ростовская область': 'Ростовская область',
    'Республика Башкортостан': 'Башкортостан',
    'Новосибирская область': 'Новосибирская область',
    'Нижегородская область': 'Нижегородская область',
    'Тюменская область': 'Тюменская область',
    'Ставропольский край': 'Ставропольский край',
    'Пермский край': 'Пермский край',
    'Красноярский край': 'Красноярский край',
    'Воронежская область': 'Воронежская область',
    'Саратовская область': 'Саратовская область',
    'Кемеровская область': 'Кемеровская область',
    'Иркутская область': 'Иркутская область',
    'Волгоградская область': 'Волгоградская область',
    'Калининградская область': 'Калининградская область',
    'Алтайский край': 'Алтайский край',
    'Ханты-Мансийский  авт. округ - Югра': 'Ханты-Мансийский АО',
    'Белгородская область': 'Белгородская область',
    'Ленинградская область': 'Ленинградская область',
    'Удмуртская Республика': 'Удмуртия',
    'Омская область': 'Омская область',
    'Тульская область': 'Тульская область',
    'Тульская область': 'Тульская область',
    'Ярославская область': 'Ярославская область',
    'Кировская область': 'Кировская область',
    'Ульяновская область': 'Ульяновская область',
    'Пензенская область': 'Пензенская область',
    'Ивановская область': 'Ивановская область',
    'Вологодская область': 'Вологодская область',
    'Брянская область': 'Брянская область',
    'Республика Коми': 'Коми',
    'Калужская область': 'Калужская область',
    'Липецкая область': 'Липецкая область',
    'Томская область': 'Томская область',
    'Смоленская область': 'Смоленская область',
    'Костромская область': 'Костромская область',
    'Курская область': 'Курская область',
    'Орловская область': 'Орловская область',
    'Республика Карелия': 'Карелия',
    'Республика Мордовия': 'Мордовия',
    'Республика Адыгея': 'Адыгея',
    'Приморский край': 'Приморский край',
    'Республика Алтай': 'Алтай',
}
region_salary = pd.read_excel('../data/enrichment/t2(1).xlsx', sheet_name='с 2019', engine='openpyxl').iloc[:-2]
region_salary = region_salary.set_index('Unnamed: 0').stack().reset_index().rename(columns={'level_1': 'date_salary', 0: 'salary', 'Unnamed: 0': 'region'})
region_salary['date_salary'] = region_salary['date_salary'].astype('str')
region_salary['salary'] = region_salary['salary'].astype('int')
# сопоставляем накзвания регионов (поскольку они могут отличаться от официального названия)
region_salary['region'] = region_salary['region'].apply(lambda x: x.strip()).map(region_map_dict)
# дропаем все, что не сопоставилось
region_salary = region_salary.dropna(subset=['region'])
region_salary['shift_month_avg_salary'] = (region_salary.sort_values(by='date_salary').groupby('region')['salary'].shift(4))
# дропаем все, что осталось после свига как np.nan
region_salary = region_salary.dropna(subset=['shift_month_avg_salary'])

In [10]:
region_salary = region_salary[['date_salary', 'region', 'shift_month_avg_salary']]
train = train.merge(region_salary, left_on=['date_start_month', 'region'], right_on=['date_salary', 'region'])
test = test.merge(region_salary, left_on=['date_start_month', 'region'], right_on=['date_salary', 'region'], sort=False, how='left')

## Feature Engineering

### Базовые признаки

In [11]:
def osm_mask_with_infrastructure(df, prefix, values, dist_list):
    """
    Функция возвращающая флаг, какие записи в округе содержат определенное кол-во зданий.
    """
    query = ' or '.join([
        f'`{prefix}_{dist}` >= {min_building}'
        for dist, min_building in zip(dist_list, values)])
    true_indexes = df.query(query).index
    mask = df.index.isin(true_indexes).astype('int')
    return mask

In [12]:
# базовое значение для признаков OSM
dist_list = ['0.001', '0.005', '0.0075', '0.01']
# базовые значения которые памятся на расстояние
values = [2, 5, 7, 10]
# заполняем train и test поочереди
for X in [train, test]:
    osm_prefix = 'osm_shops_points_in'
    X['cat_many_shops'] = osm_mask_with_infrastructure(X, osm_prefix, values, dist_list)
    osm_prefix = 'osm_leisure_points_in'
    X['cat_many_entertainment'] = osm_mask_with_infrastructure(X, osm_prefix, [1, 2, 3], dist_list[1:])
    osm_prefix = 'osm_historic_points_in'
    X['cat_many_history'] = osm_mask_with_infrastructure(X, osm_prefix, [1, 2, 3], dist_list[1:])
    osm_prefix = 'osm_transport_stop_points_in'
    X['cat_many_transports'] = osm_mask_with_infrastructure(X, osm_prefix, [1, 2, 3], dist_list[1:])
    osm_prefix = 'osm_culture_points_in'
    X['cat_many_culture_points'] = osm_mask_with_infrastructure(X, osm_prefix, [1, 2, 2], dist_list[1:])
    osm_prefix = 'osm_amenity_points_in'
    X['cat_many_amenity_points'] = osm_mask_with_infrastructure(X, osm_prefix, [1, 1, 1], dist_list[1:])
    

# преобразование переменных и создание новых категориальных
for X in [train, test]:
    X['total_square'] = np.log1p(X['total_square'])
    X['osm_city_closest_dist'] = np.log1p(X['osm_city_closest_dist'])
    X['cat_is_moscow'] = (X['region'] == 'Москва').astype(int)
    X['cat_is_moscow_oblast'] = (X['region'] == 'Московская область').astype(int)
    X['cat_is_other_region'] = (~X['region'].isin(['Москва', 'Московская область'])).astype(int)

In [13]:
# посчитаем на трейне статистику по ценам на регионе
region_aggregate = (full_train.groupby(['region'])[TARGET]
                    .agg(['min', 'max', 'median'])
                    .reset_index()
                    .rename(columns={
                        'min': 'min_region_price', 
                        'max': 'max_region_price', 
                        'median': 'median_region_price'
                    }))
train = train.merge(region_aggregate, on=['region'])
test = test.merge(region_aggregate, on=['region'], how='left')

### На основе новых признаков

In [14]:
# соотношение медианной цены в регионе и зарпалы
train['fraction_price_salary'] = train['median_region_price'] / train['shift_month_avg_salary']
test['fraction_price_salary'] = test['median_region_price'] / test['shift_month_avg_salary']

# Обучение

## Итоговая подготовка данных

In [15]:
# выделим таргет и перегруппируем в единный формат данные
target = train['per_square_meter_price'].values
data = pd.concat(
    [
        train.drop('per_square_meter_price', axis=1),
        test
    ], axis=0
).reset_index(drop=True)
# так как улица не привяза к городу, нужно делать связку город+улица, но это слишком огромное количество фичей получится
# поэтому просто дропнем
data = data.drop(['street'], axis=1)

In [16]:
# выделим категориальные фичи
categor_features = ['city', 'osm_city_nearest_name', 'region']

# избавимся от символов, так как значение признака пойдет в его название
data['city'] = data['city'].apply(lambda x: re.sub('[^A-ZА-Яа-яa-z0-9_]+', '', x))
data['osm_city_nearest_name'] = data['osm_city_nearest_name'].apply(lambda x: re.sub('[^A-ZА-Яа-яa-z0-9_]+', '', x))
data['region'] = data['region'].apply(lambda x: re.sub('[^A-ZА-Яа-яa-z0-9_]+', '', x))

# one hot encoding категориальных признаков
for feat in categor_features:
    data_temp = pd.get_dummies(data[feat], drop_first=True)
    data.drop(feat, axis=1, inplace=True)
    data_temp.columns = [feat + '_' + str(col) for col in list(data_temp)]
    data = pd.concat([data, data_temp], axis=1)

In [17]:
train = data[data['id'].isin(train['id'])]
test = data[data['id'].isin(test['id'])]
target = target.copy()

In [18]:
FEATURES = [
     'total_square',
     'floor',
     'osm_crossing_closest_dist',
     'osm_transport_stop_closest_dist',
     'shift_month_avg_salary',
     'osm_amenity_points_in_0.005',
     'osm_city_closest_dist',
     'fraction_price_salary',
     'osm_amenity_points_in_0.001',
     'reform_house_population_1000',
     'osm_train_stop_closest_dist',
     'reform_house_population_500',
     'osm_amenity_points_in_0.0075',
     'osm_crossing_points_in_0.005',
     'reform_mean_floor_count_500',
     'reform_mean_floor_count_1000',
     'osm_subway_closest_dist',
     'reform_count_of_houses_1000',
     'reform_mean_year_building_1000',
     'realty_type',
     'osm_amenity_points_in_0.01',
     'reform_mean_year_building_500',
     'osm_crossing_points_in_0.0075',
     'reform_count_of_houses_500',
     'osm_crossing_points_in_0.01',
     'osm_catering_points_in_0.005',
     'osm_transport_stop_points_in_0.005',
     'osm_transport_stop_points_in_0.0075',
     'osm_transport_stop_points_in_0.01',
     'osm_catering_points_in_0.0075',
     'osm_shops_points_in_0.005',
     'osm_catering_points_in_0.01',
     'osm_shops_points_in_0.01',
     'osm_shops_points_in_0.0075',
     'osm_leisure_points_in_0.01',
     'osm_healthcare_points_in_0.005',
     'osm_crossing_points_in_0.001',
     'osm_finance_points_in_0.005',
     'osm_healthcare_points_in_0.0075',
     'osm_healthcare_points_in_0.01',
     'osm_city_nearest_population',
     'osm_finance_points_in_0.0075',
     'osm_leisure_points_in_0.005',
     'osm_culture_points_in_0.01',
     'osm_leisure_points_in_0.0075',
     'osm_finance_points_in_0.01',
     'osm_culture_points_in_0.005',
     'osm_historic_points_in_0.0075',
     'osm_historic_points_in_0.01',
     'osm_offices_points_in_0.005',
     'osm_historic_points_in_0.005',
     'osm_catering_points_in_0.001',
     'osm_offices_points_in_0.01',
     'osm_offices_points_in_0.0075',
     'osm_culture_points_in_0.0075',
     'osm_shops_points_in_0.001',
     'osm_hotels_points_in_0.0075',
     'osm_hotels_points_in_0.01',
     'osm_hotels_points_in_0.005',
     'osm_building_points_in_0.01',
     'max_region_price',
     'median_region_price',
     'osm_building_points_in_0.005',
     'min_region_price',
     'osm_building_points_in_0.0075',
     'osm_offices_points_in_0.001',
     'osm_finance_points_in_0.001',
     'osm_culture_points_in_0.001',
     'cat_many_entertainment',
     'osm_train_stop_points_in_0.005',
     'osm_train_stop_points_in_0.0075',
     'osm_train_stop_points_in_0.01',
     'cat_many_shops'
]

## Подбор гиперпараметров

In [19]:
import optuna
from optuna.samplers import TPESampler

In [24]:
def create_model(trial):
    num_leaves = trial.suggest_int("num_leaves", 2, 1500)
    n_estimators = trial.suggest_int("n_estimators", 10, 1000)
    max_depth = trial.suggest_int('max_depth', 2, 25)
    min_child_samples = trial.suggest_int('min_child_samples', 2, 3000)
    learning_rate = trial.suggest_uniform('learning_rate', 0.00001, 0.99)
    min_data_in_leaf = trial.suggest_int('min_data_in_leaf', 2, 300)
    feature_fraction = trial.suggest_uniform('feature_fraction', 0.00001, 1.0)
    
    model = lgbm.LGBMRegressor(
        num_leaves=num_leaves,
        n_estimators=n_estimators, 
        max_depth=max_depth, 
        min_child_samples=min_child_samples, 
        min_data_in_leaf=min_data_in_leaf,
        learning_rate=learning_rate,
        feature_fraction=feature_fraction,
        random_state=13,
        n_jobs=-1
    )
    return model


def objective(trial):
    model = create_model(trial)
    X_train, X_test, y_train, y_test = train_test_split(train[FEATURES], target, random_state=random.randint(1, 10000))
    model.fit(X_train, np.log1p(y_train))
    result = np.expm1(model.predict(X_test))
    score = deviation_metric(y_test, result)
    return score

In [26]:
sampler = TPESampler(seed=13)
# раскоментить надо последние 3 строчки для запуска оптимизатора, результат у меня вышел, показанный ниже
study = optuna.create_study(direction="minimize", sampler=sampler)
study.optimize(objective, n_trials=5_000)
params_lgbm = study.best_params
print(params_lgbm)

[I 2021-09-26 02:20:28,978] A new study created in memory with name: no-name-eb410b89-121e-4346-bbe7-dd1f86f5573b
[I 2021-09-26 02:20:29,225] Trial 0 finished with value: 1.9781041999797977 and parameters: {'num_leaves': 1167, 'n_estimators': 245, 'max_depth': 21, 'min_child_samples': 2898, 'learning_rate': 0.9628753767547054, 'min_data_in_leaf': 137, 'feature_fraction': 0.6090463723366503}. Best is trial 0 with value: 1.9781041999797977.


[LightGBM] [Warning] feature_fraction is set=0.857062371977773, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.857062371977773
[LightGBM] [Warning] min_data_in_leaf is set=19, min_child_samples=107 will be ignored. Current value: min_data_in_leaf=19


[I 2021-09-26 02:20:31,445] Trial 1 finished with value: 1.2924860339222304 and parameters: {'num_leaves': 1164, 'n_estimators': 645, 'max_depth': 19, 'min_child_samples': 107, 'learning_rate': 0.29547199168557875, 'min_data_in_leaf': 19, 'feature_fraction': 0.857062371977773}. Best is trial 1 with value: 1.2924860339222304.


[LightGBM] [Warning] feature_fraction is set=0.9490946907363935, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9490946907363935
[LightGBM] [Warning] min_data_in_leaf is set=109, min_child_samples=1044 will be ignored. Current value: min_data_in_leaf=109


[I 2021-09-26 02:20:31,957] Trial 2 finished with value: 1.4419805680555324 and parameters: {'num_leaves': 560, 'n_estimators': 683, 'max_depth': 8, 'min_child_samples': 1044, 'learning_rate': 0.009328548252458909, 'min_data_in_leaf': 109, 'feature_fraction': 0.9490946907363935}. Best is trial 1 with value: 1.2924860339222304.


...

[LightGBM] [Warning] feature_fraction is set=0.46231860985899653, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.46231860985899653
[LightGBM] [Warning] min_data_in_leaf is set=7, min_child_samples=2707 will be ignored. Current value: min_data_in_leaf=7


[I 2021-09-26 05:24:51,265] Trial 4998 finished with value: 1.1166354826932414 and parameters: {'num_leaves': 852, 'n_estimators': 710, 'max_depth': 25, 'min_child_samples': 2707, 'learning_rate': 0.01839345238771304, 'min_data_in_leaf': 7, 'feature_fraction': 0.46231860985899653}. Best is trial 2497 with value: 1.0520338585112996.


[LightGBM] [Warning] feature_fraction is set=0.3548065683374708, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.3548065683374708
[LightGBM] [Warning] min_data_in_leaf is set=21, min_child_samples=2320 will be ignored. Current value: min_data_in_leaf=21


[I 2021-09-26 05:24:52,966] Trial 4999 finished with value: 1.220658343618989 and parameters: {'num_leaves': 812, 'n_estimators': 692, 'max_depth': 15, 'min_child_samples': 2320, 'learning_rate': 0.040265835158668196, 'min_data_in_leaf': 21, 'feature_fraction': 0.3548065683374708}. Best is trial 2497 with value: 1.0520338585112996.


{'num_leaves': 814, 'n_estimators': 513, 'max_depth': 24, 'min_child_samples': 2319, 'learning_rate': 0.0174352841684339, 'min_data_in_leaf': 12, 'feature_fraction': 0.3769385910386391}


In [27]:
params_lgbm = {
    'num_leaves': 814, 
    'n_estimators': 513, 
    'max_depth': 24, 
    'min_child_samples': 2319, 
    'learning_rate': 0.0174352841684339,
    'min_data_in_leaf': 12, 
    'feature_fraction': 0.3769385910386391
}

In [28]:
# params_lgbm = {
#     'num_leaves': 1452,/
#     'n_estimators': 203,
#     'max_depth': 7,
#     'min_child_samples': 1065,
#     'learning_rate': 0.06413626913234637,
#     'min_data_in_leaf': 8,
#     'feature_fraction': 0.5710701270344902
# }

## Подбор коэффициентов

In [30]:
%%time

# обозначим коэффициенты среди которых будем подбирать и трешхолд, который дополнительно будем скалировать
coefficients = [0.88, 0.89, 0.9, 0.91, 0.92, 0.93]
thresholds = [150000, 175000, 200000, 225000, 250000]

# Будем идти по 5 фолдам, внутри которого разные random_state для разбития
n_splits = 5
random_states = [13, 666, 228, 777, 42]

# заведем модель
model = lgbm.LGBMRegressor(**params_lgbm)

# прохождение в цикле по параметрам
for coeff in coefficients:
    for thr in thresholds:
        print(f'coeff: {coeff}')
        print(f'thr: {thr}')
        # финальный показатель метрики
        final_loss = list()
        for fold_num, random_state in enumerate(random_states):
            kFold = KFold(n_splits=n_splits, shuffle=True, random_state=random_state)
            total_loss = list()
            for iteration, (train_index, valid_index) in enumerate(kFold.split(train, target)):
                X_train = train.iloc[train_index].reset_index(drop=True)
                X_valid = train.iloc[valid_index].reset_index(drop=True)
                y_train = target[train_index]
                y_valid = target[valid_index]
                # для обучения используем логарифмирование
                model.fit(X_train[FEATURES], np.log1p(y_train), verbose=-100)
                # финальное предсказание преобразуем с помощью expm1 к изнакальному виду
                valid_pred = np.expm1(model.predict(X_valid[FEATURES]))
                # применим коэффициенты и посчитаем loss
                valid_pred *= coeff
                valid_pred[valid_pred > thr] = valid_pred[valid_pred > thr] * coeff 
                loss = deviation_metric(y_valid, valid_pred)
                total_loss.append(np.mean(loss))
            final_loss.append(np.mean(total_loss))

            print(f'Fold({["1-10", "11-20", "21-30", "31-40", "41-50"][fold_num]}) deviation_metric: {np.mean(total_loss)}')
        print(f'Final deviation_metric: {np.mean(final_loss)}')
        print()
        print('*'*100)

coeff: 0.88
thr: 150000
[LightGBM] [Warning] feature_fraction is set=0.3769385910386391, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.3769385910386391
[LightGBM] [Warning] min_data_in_leaf is set=12, min_child_samples=2319 will be ignored. Current value: min_data_in_leaf=12
[LightGBM] [Warning] feature_fraction is set=0.3769385910386391, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.3769385910386391
[LightGBM] [Warning] min_data_in_leaf is set=12, min_child_samples=2319 will be ignored. Current value: min_data_in_leaf=12
[LightGBM] [Warning] feature_fraction is set=0.3769385910386391, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.3769385910386391
[LightGBM] [Warning] min_data_in_leaf is set=12, min_child_samples=2319 will be ignored. Current value: min_data_in_leaf=12
[LightGBM] [Warning] feature_fraction is set=0.3769385910386391, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.37693

KeyboardInterrupt: 

## Итоговый сабмит

In [33]:
%%time

# Будем идти по 5 фолдам, внутри которого разные random_state для разбития
kFold_random_state = [13, 666, 228, 777, 42]
n_splits = 5

# запишем лучшие параметры
coeff = 1
thr = 1

# заведем модель
model = lgbm.LGBMRegressor(**params_lgbm)

# файл для записи финального результата
submission = test_submission.copy()
submission.iloc[:, 1] = 0

final_loss = list()
for ind_k, random_state in enumerate(kFold_random_state):
    kFold = KFold(n_splits=n_splits, shuffle=True, random_state=random_state)
    total_loss = list()
    for iteration, (train_index, valid_index) in enumerate(kFold.split(train, target)):

        X_train = train.iloc[train_index].reset_index(drop=True)
        X_valid = train.iloc[valid_index].reset_index(drop=True)
        y_train = target[train_index]
        y_valid = target[valid_index]
        # для обучения используем логарифмирование
        model.fit(X_train[FEATURES], np.log1p(y_train), verbose=-100)
        # финальное предсказание преобразуем с помощью expm1 к изнакальному виду
        valid_pred = np.expm1(model.predict(X_valid[FEATURES]))
        # применим коэффициенты и посчитаем loss
        valid_pred *= coeff
        valid_pred[valid_pred > thr] = valid_pred[valid_pred > thr] * coeff 
        loss = deviation_metric(y_valid, valid_pred)
        # запишем результат
        predict = np.expm1(model.predict(test[FEATURES]))
        submission['per_square_meter_price'] = (submission['per_square_meter_price'] + predict / (len(kFold_random_state)*n_splits))
        total_loss.append(np.mean(loss))
    final_loss.append(np.mean(total_loss))
    print(f'Fold({["1-10", "11-20", "21-30", "31-40", "41-50"][ind_k]}) deviation_metric: {np.mean(total_loss)}')
print(f'Final deviation_metric: {np.mean(final_loss)}')

[LightGBM] [Warning] feature_fraction is set=0.3769385910386391, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.3769385910386391
[LightGBM] [Warning] min_data_in_leaf is set=12, min_child_samples=2319 will be ignored. Current value: min_data_in_leaf=12
[LightGBM] [Warning] feature_fraction is set=0.3769385910386391, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.3769385910386391
[LightGBM] [Warning] min_data_in_leaf is set=12, min_child_samples=2319 will be ignored. Current value: min_data_in_leaf=12
[LightGBM] [Warning] feature_fraction is set=0.3769385910386391, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.3769385910386391
[LightGBM] [Warning] min_data_in_leaf is set=12, min_child_samples=2319 will be ignored. Current value: min_data_in_leaf=12
[LightGBM] [Warning] feature_fraction is set=0.3769385910386391, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.3769385910386391
[LightGBM] [

In [34]:
submission_raw = submission.copy()

# немного подрежем выбросы сверху с помощью имующихся коэффициентов
submission_raw['per_square_meter_price'] = submission_raw['per_square_meter_price'] * coeff

submission_raw.loc[submission_raw['per_square_meter_price'] >= thr, 'per_square_meter_price'] \
    = submission_raw.loc[submission_raw['per_square_meter_price'] >= thr, 'per_square_meter_price'] * coeff
submission_raw.to_csv('final_submission_0.92_150000_v2.csv', index=False)